# *Calculation of phase noise and key rates for some relevant QKD protocols*

Figures for paper "Phase Noise in Real-World Twin-Field Quantum Key Distribution"
G. Bertaina, C. Clivati, S. Donadello, C. Liorni, A. Meda, S. Virzì, M. Gramegna, M. Genovese, F. Levi, D. Calonico, M. Dispenza, and I. P. Degiovanni

When using this simulator and/or imported datasets, please cite the final journal reference found at https://arxiv.org/abs/2310.08621 

In [ ]:
import time
import datetime
import os
import copy

# Scientific
import numpy as np
import math

# Graphics
import matplotlib as mpl
import matplotlib.pyplot as plt
from matplotlib import ticker as mticker
from matplotlib import rcParams

fsize = 12
legfontsize = 10
plt.rc('xtick', labelsize = fsize)
plt.rc('ytick', labelsize = fsize)
plt.rc('axes', labelsize = fsize)

rcParams.update({
  "figure.dpi": 300,
  'text.usetex': True,
  'text.latex.preamble': r'\usepackage{amsfonts,nicefrac}',
  'mathtext.fontset': "stix",
  'font.family': 'STIXGeneral'
})

# Noise spectrum

In [ ]:
# Gain loop   Eq F4
def G1(f):
  B0 = 300e3 
  gamma = 0.1 
  delta = 10 

  G0 = (2*np.pi*B0)**2 * (1+delta) / (1+gamma)
  
  return G0/(2*np.pi*f*1j)**2 * (1j*f + B0*gamma)/(1j*f + B0*delta)

# Reference laser phase noise Eq F1
def freelasnoise(f):
    rm3 = 3e6 
    rm2 = 3e2 
    fc = 2e6 
    return rm3/f**3 + rm2/f**2 * (fc/(f+fc))**2
  
# Cavity noise Eq F3
def cavitynoise(f):
    Cm4 = 0.5 
    Cm3 = 0 
    Cm2 = 2e-3 
    return Cm4/f**4 + Cm3/f**3 + Cm2/f**2

# Cavity stabilized reference laser noise Eq F2
def stablasnoise(f):
  return cavitynoise(f) + freelasnoise(f) * np.abs(1 / (1 + G1(f)))**2

# Free fiber noise Eq 6
def freefibnoise(f,L):
    l0 = 44 
    f1c = 100 
    return l0*L/f**2 * (f1c/(f+f1c))**2
  
# Stabilized fiber noise Eq 8
def stabfibnoise(f,L):
    l0 = 44 
    ls = 1543.33 
    lq = 1542.14 
    return ((ls-lq)/ls)**2 * l0*L/f**2

# Fiber detection noise App G
def fiberdetection(f):
    s0 = 1e-8 
    f2c = 200e3 
    return s0*(f2c/(f+f2c))**2
  
# Evaluates spectra in different setups as described in the paper 
def calc_spectra(comm=True, cavity=True, stab=True):
    # Parameters
    c0 = 299792458.0/1000. # km/s speed of light in vacuum
    n0 = 1.45 # index of refraction of fiber

    # Fiber noise 
    # Eq 6
    Sf_free = lambda f,L: freefibnoise(f,L)
    # Eq 8
    Sf_stab = lambda f,L: stabfibnoise(f,L)

    if stab:
        Sf = Sf_stab
        # Eq App G
        Sf_det = lambda f: fiberdetection(f)
    else:
        Sf = Sf_free
        Sf_det = lambda f: 0 

    # Reference laser phase noise Eq F1
    Sref = lambda f: freelasnoise(f)

    # Eq F2
    Scav_stab = lambda f: stablasnoise(f)

    if cavity:
        Slas = Scav_stab
    else:
        Slas = Sref

    if comm:
        # Common-laser Eq 5
        Slas_fin = lambda f,LB,deltaL: 4 * (np.sin(2*np.pi * f * n0 * deltaL / c0))**2 * Slas(f)
        Sf_fin = lambda f,LB,deltaL: 4 * (Sf(f,LB) + Sf(f,LB+deltaL)) + Sf_det(f)
    else:
        # Independent lasers Eq 7
        Slas_fin = lambda f,LB,deltaL: Slas(f) + Slas(f)
        Sf_fin = lambda f,LB,deltaL: Sf(f,LB) + Sf(f,LB+deltaL) + Sf_det(f)

    Sphi = lambda f,LB,deltaL: Slas_fin(f,LB,deltaL) + Sf_fin(f,LB,deltaL)

    return Sphi, Slas_fin, Sf_fin
  
  
# Integrates spectra to get sigma_phi as a function of the tauQ cutoff  
def calc_sigma(Sphi, LB, deltaL, num=1000):
    fhigh=1e6
    fstart=-3
    fstop=6
    f = np.logspace(fstart, fstop, num)
    cond = f <= fhigh
    sigma_lst = np.cumsum((Sphi(f[cond],LB,deltaL)[1:] * np.diff(f[cond]))[::-1])**0.5
    tQ_lst = 1/f[cond][1:][::-1]
    return tQ_lst, sigma_lst
  
# Finds at which tauQ the noise standard deviation reaches a certain limit
def calc_sigma_tau(comm, cavity, stab, deltaL, LB, sigma_lim):
  
    Sphi, Slas_fin, Sf_fin = calc_spectra(comm, cavity, stab)
    maxnumt=10000
    tQ_lst, sigma_lst = calc_sigma(Sphi, LB=LB, deltaL=deltaL, num=maxnumt)

    arr = np.where(np.diff(np.sign(sigma_lst-sigma_lim)))[0]
    if (len(arr) == 0):
      r=maxnumt-2
    else:
      r=arr[0]
    
    return tQ_lst[r], deltaL, sigma_lst[r]
  
# Finds at which tauQ the noise standard deviation reaches a certain limit
# Depending on the total loss
def calc_sigma_tau_loss(comm, cavity, stab, deltaL, totdBloss, alpha, sigma_lim):
  
    totL = totdBloss/alpha # Equivalent total distance. We assume it is twice the longest branch LA (if LA>LB then an attenuator is added along LB)
    LA = totL/2
    LB = LA - deltaL
    if (LB<0):
      raise("LB cannot be negative: Increase loss or reduce deltaL")
  
    Sphi, Slas_fin, Sf_fin = calc_spectra(comm, cavity, stab)
    maxnumt=10000
    tQ_lst, sigma_lst = calc_sigma(Sphi, LB=LB, deltaL=deltaL, num=maxnumt)

    arr = np.where(np.diff(np.sign(sigma_lst-sigma_lim)))[0]
    if (len(arr) == 0):
      r=maxnumt-2
    else:
      r=arr[0]
    
    return tQ_lst[r], deltaL, sigma_lst[r], totdBloss

# Laser and fiber noise spectra FIGURES 5 and 6

In [ ]:
def plot_laser_fiber_spectra():
  LToBardonecchia=114 # Km
    
  fmod=np.logspace(-1,6,10000)

  fig=plt.figure(figsize=(4.7,2.8))
  f_stable_laser_meas,stable_laser_meas=np.genfromtxt('stable_laser_meas.txt',unpack=True,comments='#')
  f_free_laser_meas,free_laser_meas=np.genfromtxt('free_laser_meas.txt',unpack=True,comments='#')

  plt.loglog(fmod,freelasnoise(fmod),color='C0',label='Free-running laser')
  plt.loglog(f_free_laser_meas,free_laser_meas,color='C0',alpha=0.4)
  plt.loglog(fmod,stablasnoise(fmod),color='C1',label='Stabilized laser')
  plt.loglog(f_stable_laser_meas,stable_laser_meas,color='C1',alpha=0.4)

  plt.xlabel('Frequency [Hz]')
  plt.ylabel(r'Phase noise [rad$^2$ Hz$^{-1}$]')
  plt.xlim(10,1e6)
  plt.ylim(1e-10,100)
  plt.grid()
  plt.legend(fontsize = legfontsize)
  plt.tight_layout()
  plt.savefig("Lasnoise.pdf", bbox_inches='tight')

  fig=plt.figure('Fibnoise',figsize=(4.7,2.8))
  f_stable_fiber_meas,stable_fiber_meas=np.genfromtxt('stable_fiber_meas.txt',unpack=True,comments='#')
  f_free_fiber_meas,free_fiber_meas=np.genfromtxt('free_fiber_meas.txt',unpack=True,comments='#')

  # Factor 4 due to round-trip in measurement
  plt.loglog(fmod,4*freefibnoise(fmod,LToBardonecchia),color='C0',label='Free-running fiber')
  plt.loglog(f_free_fiber_meas,free_fiber_meas,color='C0',alpha=0.4)
  plt.loglog(fmod,4*stabfibnoise(fmod,LToBardonecchia)+fiberdetection(fmod),color='C1',label='Stabilized fiber')
  plt.loglog(f_stable_fiber_meas,stable_fiber_meas,color='C1',alpha=0.4)
  

  plt.xlabel('Frequency [Hz]')
  plt.ylabel(r'Phase noise [rad$^2$ Hz$^{-1}$]')
  plt.xlim(10,1e6)
  plt.ylim(1e-10,100)
  plt.grid()
  plt.legend(fontsize = legfontsize)
  plt.tight_layout()
  plt.savefig("Fibnoise.pdf", bbox_inches='tight')
  
plot_laser_fiber_spectra()

# Definition of phase stabilization scenarios

In [ ]:
deltaLmin = 0.020 # 20m minimal path difference
deltaLmax = 2.5 # 2.5km max path difference
LBref = 100 # km reference shortest branch
max_sigma_phi = 0.2 # rad -> QBER ~ sigma_phi^2/4 ~ 1% Conservative reference QBER

Scenario1={"comm":True, "cavity":False, "stab":False, "deltaL":deltaLmin}
Scenario2={"comm":True, "cavity":False, "stab":True, "deltaL":deltaLmin}
Scenario3={"comm":True, "cavity":False, "stab":True, "deltaL":deltaLmax}
Scenario3b={"comm":True, "cavity":False, "stab":False, "deltaL":deltaLmax}
Scenario4={"comm":True, "cavity":True, "stab":False, "deltaL":deltaLmax}
Scenario5={"comm":True, "cavity":True, "stab":True, "deltaL":deltaLmax}
Scenario6={"comm":False, "cavity":True, "stab":False, "deltaL":deltaLmax}
Scenario7={"comm":False, "cavity":True, "stab":True, "deltaL":deltaLmax}


# Reference scenarios with specific shortest branch
LB=LBref
scen_lst = []
scen_lst.append(calc_sigma_tau(Scenario1["comm"], Scenario1["cavity"], Scenario1["stab"], Scenario1["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario2["comm"], Scenario2["cavity"], Scenario2["stab"], Scenario2["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario3["comm"], Scenario3["cavity"], Scenario3["stab"], Scenario3["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario3b["comm"], Scenario3b["cavity"], Scenario3b["stab"], Scenario3b["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario4["comm"], Scenario4["cavity"], Scenario4["stab"], Scenario4["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario5["comm"], Scenario5["cavity"], Scenario5["stab"], Scenario5["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario6["comm"], Scenario6["cavity"], Scenario6["stab"], Scenario6["deltaL"], LB=LB, sigma_lim=max_sigma_phi))
scen_lst.append(calc_sigma_tau(Scenario7["comm"], Scenario7["cavity"], Scenario7["stab"], Scenario7["deltaL"], LB=LB, sigma_lim=max_sigma_phi))

scen_lst = np.array(scen_lst)

# Plot phase noise as a function of tauQ and deltaL FIGURES 2 and 7

In [ ]:
def plot_sigma(comm, cavity, stab, LB, fig=None, ax=None, dLstart=-2, dLstop=2, dLnum=100, sigma_lim=[max_sigma_phi], linestyles="-", cmap="GnBu", colorbarax=None, xlabel=True, ylabel=True, manual=None):
    if ax is None:
        fig, ax = plt.subplots(1, 1)
    deltaL_lst = np.logspace(dLstart, dLstop, dLnum)
    tQ_lst = []
    sigma = []
    for deltaL in deltaL_lst:
        Sphi, Slas_fin, Sf_fin = calc_spectra(comm, cavity, stab)
        tQ_lst, sigma_lst = calc_sigma(Sphi,LB, deltaL)
        sigma.append(sigma_lst)
    sigma = np.array(sigma)

    cm = ax.pcolormesh(tQ_lst, deltaL_lst, sigma, cmap=cmap, rasterized=True,
                norm=mpl.colors.LogNorm(vmin=0.01, vmax=10))
    ax.set_xscale("log")
    ax.set_yscale("log")
    if xlabel:
        ax.set_xlabel(r"$\tau_\mathrm{Q}$ [s]")
    if ylabel:
        ax.set_ylabel(r"$\Delta L$ [km]")
    if colorbarax is not None:
        fig.colorbar(cm, ax=colorbarax, label=r"$\sigma_\varphi$ [rad]", location="top", shrink=0.3, extend='max')
    cs = ax.contour(tQ_lst, deltaL_lst, sigma, sigma_lim, linestyles=linestyles, linewidths=1.5, colors='C3')
    ax.clabel(cs, inline=True, fontsize=legfontsize, fmt=r"%.1g$\,$rad", inline_spacing=14, manual=manual)
    
    return tQ_lst, deltaL_lst, sigma, ax
    
def plot2_sigma(comm, cavity, stab, LB, ax, dLstart=-2, dLstop=2, dLnum=100, sigma_lim=max_sigma_phi, clablcolors=None, fmt=r"%.1f$\,$rad", **kwargs):
    deltaL_lst = np.logspace(dLstart, dLstop, dLnum)
    tQ_lst = []
    sigma = []
    for deltaL in deltaL_lst:
        Sphi, Slas_fin, Sf_fin = calc_spectra(comm, cavity, stab)
        tQ_lst, sigma_lst = calc_sigma(Sphi,LB, deltaL)
        sigma.append(sigma_lst)
    sigma = np.array(sigma)

    ax.set_xscale("log")
    ax.set_yscale("log")
    ax.set_xlabel(r"$\tau_\mathrm{Q}$ [s]")
    cs = ax.contour(tQ_lst, deltaL_lst, sigma, [sigma_lim], **kwargs)
    lab=ax.clabel(cs, inline=True, fontsize=fsize, fmt=r"%.1g$\,$rad", colors=clablcolors, inline_spacing=12, manual=[(1e-4,1.5e1)])
    for l in lab:
      l.set_rotation(270)
    return tQ_lst, deltaL_lst, sigma, ax
  
def plot_main_sigma_deltaL():
  fig, ax = plt.subplots(1, 3, figsize=(11,3), sharey=True, sharex=True)

  _lw = [1.5, 1.5]
  _co = ["C1", "C2"]
  _ls = ["-", (0, (4, 2))]

  tQ_lst, deltaL_lst, sigma, _ = \
  plot2_sigma(Scenario4["comm"], Scenario4["cavity"], Scenario4["stab"], LB=LBref, ax=ax[0], colors=_co[1], linestyles=[_ls[0]], linewidths=_lw[1])
  plot2_sigma(Scenario1["comm"], Scenario1["cavity"], Scenario1["stab"], LB=LBref, ax=ax[0], colors=_co[1], linestyles=[_ls[1]], linewidths=_lw[1])

  plot2_sigma(Scenario5["comm"], Scenario5["cavity"], Scenario5["stab"], LB=LBref, ax=ax[1], colors=_co[0], linestyles=[_ls[0]], linewidths=_lw[0], sigma_lim=max_sigma_phi)
  plot2_sigma(Scenario2["comm"], Scenario2["cavity"], Scenario2["stab"], LB=LBref, ax=ax[1], colors=_co[0], linestyles=[_ls[1]], linewidths=_lw[0], sigma_lim=max_sigma_phi)

  plot2_sigma(Scenario6["comm"], Scenario6["cavity"], Scenario6["stab"], LB=LBref, ax=ax[2], colors=_co[1], linestyles=[_ls[0]], linewidths=_lw[1])
  plot2_sigma(Scenario7["comm"], Scenario7["cavity"], Scenario7["stab"], LB=LBref, ax=ax[2], colors=_co[0], linestyles=[_ls[0]], linewidths=_lw[0])

  plot2_sigma(comm=False, cavity=False, stab=False, LB=LBref, ax=ax[2], colors=_co[1], linestyles=[(0, (4, 8))], linewidths=_lw[1], clablcolors=[(1, 1, 1, 0)])
  plot2_sigma(comm=False, cavity=False, stab=True, LB=LBref, ax=ax[2], colors=_co[0], linestyles=[(6, (4, 8))], linewidths=_lw[0])
  
  _ax_leg = 0
  ax[_ax_leg].plot([], [], color="k", linestyle=_ls[0], label="ultrastable laser", linewidth=_lw[0])
  ax[_ax_leg].plot([], [], color="k", linestyle=_ls[1], label="free-running laser", linewidth=_lw[0])

  ax[_ax_leg].plot([], [], color=_co[0], linestyle=_ls[0], label="with fiber stab.", linewidth=_lw[0])
  ax[_ax_leg].plot([], [], color=_co[1], linestyle=_ls[0], label="no fiber stab.", linewidth=_lw[1])

  _c = np.outer(np.logspace(0,1,len(tQ_lst)), np.ones_like(deltaL_lst))
  ax[0].pcolormesh(tQ_lst, deltaL_lst, _c.T, cmap="Blues", alpha=0.25, rasterized=True)
  ax[1].pcolormesh(tQ_lst, deltaL_lst, _c.T, cmap="Greens", alpha=0.25, rasterized=True)
  ax[2].pcolormesh(tQ_lst, deltaL_lst, _c.T, cmap="Purples", alpha=0.25, rasterized=True)

  ax[0].text(-0.0, 1.08, "a)",
              verticalalignment='bottom', horizontalalignment='right',
              transform=ax[0].transAxes, fontsize=fsize)
  ax[1].text(-0.0, 1.08, "b)",
              verticalalignment='bottom', horizontalalignment='right',
              transform=ax[1].transAxes, fontsize=fsize)
  ax[2].text(-0.0, 1.08, "c)",
              verticalalignment='bottom', horizontalalignment='right',
              transform=ax[2].transAxes, fontsize=fsize)

  ax[0].grid()
  ax[1].grid()
  ax[2].grid()
  ax[_ax_leg].legend(fontsize = 11,ncol=1, loc='lower right', bbox_to_anchor=(1.2, 0.11))
  ax[_ax_leg].set_zorder(9)
  ax[0].set_title("common laser,\nno fiber stabilization", fontsize=fsize)
  ax[1].set_title("common laser,\nwith fiber stabilization", fontsize=fsize)
  ax[2].set_title("independent lasers", fontsize=fsize)
  ax[0].set_ylabel(r"$\Delta L$ [km]")

  ax[0].set_xlim(1e-6, 1e1)
  ax[0].set_ylim(1e-2, 1e2)

  lscen = ["1", "2", "3", "3", "4", "5", "6", "7"]
  xscen = scen_lst[:,0]
  yscen = scen_lst[:,1]
  ascen = np.array([0, 1, 1, 0, 0, 1, 2, 2])

  for _a in [0,1,2]:
      ax[_a].scatter(xscen[ascen==_a], yscen[ascen==_a], c="C0", s=25, marker="*", zorder=8)
  for _l, _x, _y, _a in zip(lscen, xscen, yscen, ascen):
      ax[_a].annotate(_l, (_x, _y), xytext=(_x*1.5, _y*1.0), c="C0")

  ax[2].xaxis.set_minor_locator(plt.LogLocator(base=10.0, subs=[], numticks=10))
  ax[2].xaxis.set_minor_formatter(plt.NullFormatter())
  ax[0].tick_params(direction="in", which='both')
  ax[1].tick_params(direction="in", which='both')
  ax[2].tick_params(direction="in", which='both')

  plt.savefig("sigma-unbalance.pdf", bbox_inches='tight')
  

def plot_contour_sigma_deltaL():
  fig, ax2 = plt.subplots(2, 4, figsize=(10.5,6.7), sharey=False, sharex=False, layout='constrained')
  ax2 = np.array(ax2).flatten()

  ax = np.array([ax2[0], ax2[2], ax2[4], ax2[6], ax2[1], ax2[3], ax2[5], ax2[7]])

  _ = plot_sigma(Scenario1["comm"], Scenario1["cavity"], Scenario1["stab"], LB=LBref, ax=ax[0], fig=fig, sigma_lim=[max_sigma_phi], manual=[(1e-3, 0.1)])
  _ = plot_sigma(Scenario4["comm"], Scenario4["cavity"], Scenario4["stab"], LB=LBref, ax=ax[1], fig=fig, sigma_lim=[max_sigma_phi], manual=[(1e-3, 0.3)])

  _ = plot_sigma(Scenario2["comm"], Scenario2["cavity"], Scenario2["stab"], LB=LBref, ax=ax[2], fig=fig, sigma_lim=[max_sigma_phi], linestyles=["-"], manual=[(1e-2, 0.6)])
  _ = plot_sigma(Scenario5["comm"], Scenario5["cavity"], Scenario5["stab"], LB=LBref, ax=ax[3], fig=fig, colorbarax=ax2[0:4], sigma_lim=[max_sigma_phi], manual=[(1,0.3)], linestyles=["-"])

  _ = plot_sigma(comm=False, cavity=False, stab=False, LB=LBref, ax=ax[4], fig=fig, sigma_lim=[max_sigma_phi], manual=[(1e-4, 0.3)])
  _ = plot_sigma(Scenario6["comm"], Scenario6["cavity"], Scenario6["stab"], LB=LBref, ax=ax[5], fig=fig, sigma_lim=[max_sigma_phi], manual=[(1e-3, 0.3)])

  _ = plot_sigma(comm=False, cavity=False, stab=True, LB=LBref, ax=ax[6], fig=fig, sigma_lim=[max_sigma_phi], manual=[(1e-4, 0.3)])
  _ = plot_sigma(Scenario7["comm"], Scenario7["cavity"], Scenario7["stab"], LB=LBref, ax=ax[7], fig=fig, sigma_lim=[max_sigma_phi], manual=[(1,0.3)], linestyles=["-"])

  ax[0].set_title("free-running common laser,\nno fiber stabilization", fontsize=fsize)
  ax[1].set_title("ultrastable common laser,\nno fiber stabilization", fontsize=fsize)

  ax[2].set_title("free-running common laser,\nwith fiber stabilization", fontsize=fsize)
  ax[3].set_title("ultrastable common laser,\nwith fiber stabilization", fontsize=fsize)

  ax[4].set_title("free-running independent lasers,\nno fiber stabilization", fontsize=fsize)
  ax[5].set_title("ultrastable independent lasers,\nno fiber stabilization", fontsize=fsize)

  ax[6].set_title("free-running independent lasers,\nwith fiber stabilization", fontsize=fsize)
  ax[7].set_title("ultrastable independent lasers,\nwith fiber stabilization", fontsize=fsize)

  ascen = np.array([0, 2, 2, 0, 1, 3, 5, 7])
  
  lscen = ["1", "2", "3", "3", "4", "5", "6", "7"]
  xscen = scen_lst[:,0]
  yscen = scen_lst[:,1]
  
  for _a in np.arange(len(ax)):
      ax[_a].scatter(xscen[ascen==_a], yscen[ascen==_a], c="k", s=25, marker="*", zorder=8)
  for _l, _x, _y, _a in zip(lscen, xscen, yscen, ascen):
      ax[_a].annotate(_l, (_x, _y), xytext=(_x*1.5, _y*1.0))

  for _n in [1,2,3,5,6,7]:
      ax2[_n].set_ylabel(None)
      ax2[_n].yaxis.set_ticklabels([]) 

  for a in ax:
      a.set_xlim(1e-6, 1e1)
      a.set_ylim(1e-2, 1e2)
      a.xaxis.set_minor_locator(plt.LogLocator(base=10.0, subs=[], numticks=10))
      a.xaxis.set_minor_formatter(plt.NullFormatter())
      a.tick_params(direction="in", which='both')


  for _a, lab in zip(ax2, ["a)", "b)", "c)", "d)", "e)", "f)", "g)", "h)"]):
      _a.text(-0.05, 1.08, lab,
                  verticalalignment='bottom', horizontalalignment='right',
                  transform=_a.transAxes, fontsize=fsize)

  plt.savefig("sigma-unbalance-maps.pdf", bbox_inches='tight')
  

# FIGURE 2
plot_main_sigma_deltaL()

# FIGURE 7
plot_contour_sigma_deltaL()

# Plot spectra and sigma for different scenarios FIGURE 8

In [ ]:
def plot_spectra_scenarios():
  rows=7
  cols=2
  fig, axs = plt.subplots(rows,cols,figsize=(10,10))

  # Freq range
  num=1000
  fmod=np.logspace(-1,6,num);

  def plots(comm, cavity, stab, deltaL,LB,ax1,ax2 ):

    Sphi, Slas_fin, Sf_fin = calc_spectra(comm, cavity, stab)

    Sl = Slas_fin(fmod, LB=LB, deltaL=deltaL)
    Sf = Sf_fin(fmod, LB=LB, deltaL=deltaL)
    ax1.loglog(fmod,Sl,color='C0',ls='dotted',label='laser')
    ax1.loglog(fmod,Sf,color='C0',label='fiber',ls='dashed')
    ax1.loglog(fmod,Sl+Sf,color='C0',label='total',lw=2)

    times, sigmal = calc_sigma(Slas_fin,LB=LB, deltaL=deltaL, num=num)
    times, sigmaf = calc_sigma(Sf_fin,LB=LB, deltaL=deltaL, num=num)
    times, sigmat = calc_sigma(Sphi,LB=LB, deltaL=deltaL, num=num)

    ax2.loglog(times, sigmal,color='C0',ls='dotted',label='laser')
    ax2.loglog(times, sigmaf,color='C0',label='fiber',ls='dashed')
    ax2.loglog(times, sigmat,color='C0',label='total',lw=2)

    ax2.axhline(y=max_sigma_phi,ls='dashed',lw=2.,color='gray',label=r'$e_\varphi = 0.01$')    

  # SCENARIO 1 Free common laser, NO fiber stabilization, deltaL=0
  plots(Scenario1["comm"], Scenario1["cavity"], Scenario1["stab"], Scenario1["deltaL"],LBref,axs[0,0],axs[0,1])

  # SCENARIO 2 Free common laser, YES fiber stabilization, deltaL=0
  plots(Scenario2["comm"], Scenario2["cavity"], Scenario2["stab"], Scenario2["deltaL"],LBref,axs[1,0],axs[1,1])  

  # SCENARIO 3 Free common laser, ANY fiber stabilization, deltaL=2.5km
  plots(Scenario3["comm"], Scenario3["cavity"], Scenario3["stab"], Scenario3["deltaL"],LBref,axs[2,0],axs[2,1])  

  # SCENARIO 4 Ultrastable common laser, NO fiber stabilization, deltaL=2500
  plots(Scenario4["comm"], Scenario4["cavity"], Scenario4["stab"], Scenario4["deltaL"],LBref,axs[3,0],axs[3,1]) 

  # SCENARIO 5 Ultrastable common laser, YES fiber stabilization, deltaL=2500
  plots(Scenario5["comm"], Scenario5["cavity"], Scenario5["stab"], Scenario5["deltaL"],LBref,axs[4,0],axs[4,1])

  # SCENARIO 6 Ultrastable independent lasers, NO fiber stabilization, ANY deltaL
  plots(Scenario6["comm"], Scenario6["cavity"], Scenario6["stab"], Scenario6["deltaL"],LBref,axs[5,0],axs[5,1]) 

  # SCENARIO 7 Ultrastable independent lasers, YES fiber stabilization, ANY deltaL
  plots(Scenario7["comm"], Scenario7["cavity"], Scenario7["stab"], Scenario7["deltaL"],LBref,axs[6,0],axs[6,1])  

  for row in range(rows):
    axs[row,0].set_xlim(10,1e6)
    axs[row,0].set_ylim(1e-10,1e-4)
    axs[row,0].grid()
    axs[row,0].yaxis.set_minor_locator(mticker.LogLocator(numticks = 99, subs = "auto"))
    axs[row,0].tick_params(direction="in", labelbottom=False,which='both', labelsize=legfontsize,zorder=6)
    axs[row,0].set_ylabel('$S_\\varphi$ [rad$^2$ Hz$^{-1}$]', fontsize=10)
    axs[row,0].text(-0.22,0.9,f"{row+1})", transform=axs[row,0].transAxes)

    axs[row,1].set_xlim(1.e-6,1.e-1)
    axs[row,1].set_ylim(1e-2,1)
    axs[row,1].grid()
    axs[row,1].tick_params(direction="in", labelbottom=False,which='both', labelsize=legfontsize,zorder=3)
    axs[row,1].set_ylabel('$\sigma_\\varphi$ [rad]', fontsize=10)
    
  axs[3,0].legend(fontsize = legfontsize)
  axs[3,1].legend(fontsize = legfontsize)

  axs[6,0].set_xlabel('Frequency [Hz]')
  axs[6,1].set_xlabel(r'$\tau_\mathrm{Q}$ [s]')
  axs[6,1].tick_params( labelbottom=True)
  axs[6,0].tick_params( labelbottom=True)
  fig.subplots_adjust(hspace=0.2,wspace=0.2)

  plt.savefig("scenarios.pdf", bbox_inches='tight')
  
# FIGURE 8
plot_spectra_scenarios()

# Key rates of protocols

In [ ]:
# Binary entropy
def H2(p):
  ''' 0 <= p <= 1'''
  if (p<1e-15):
    return 0.0
  else:
    return -p*np.log2(p)-(1-p)*np.log2(1-p)
  
# Transmittance = Intensity ratio = ratio of surviving photons
# decreases exponentially in the distance due to losses
def etadB(dBloss):
  return 10**(-dBloss/10) # /10 because we use dB

# QBER from phase fluctuations 
def EphaseFromSigmaPhi(SigmaPhi):
  return (1-np.exp(-SigmaPhi**2/2))/2 # ~ SigmaPhi**2/4

# Signals are sent during accumulation window and not sent during the stabilization overhead
def duty_stabilization(accumulation_time,stabilization_overhead):
  phase_stabilization_window = accumulation_time+stabilization_overhead 
  duty = accumulation_time/phase_stabilization_window 
  return duty

## Secret key capacity

[S. Pirandola, R. Laurenza, C. Ottaviani, and L. Banchi, Fundamental Limits of Repeaterless Quantum Communications, Nat. Commun. 8, 1 (2017)]

[S. Pirandola, Capacities of Repeater-Assisted Quantum Communications, arXiv:1601.00966 [Cond-Mat] (2017)]

In [ ]:
def RdB_secret_key_capacity(dBloss):
  rate = -np.log2(1-etadB(dBloss))
  if (rate>1):
    rate = np.sqrt(-1)
  return rate

def RdB_realistic_secret_key_capacity(dBloss,etadet):
  rate = -np.log2(1-etadet*etadB(dBloss))
  if (rate>1):
    rate = np.sqrt(-1)
  return rate

## Decoy state QKD BB84 with phase encoding

[H.-K. Lo, X. Ma, and K. Chen, Decoy State Quantum Key Distribution, Phys. Rev. Lett. 94, 230504 (2005)]

[X. Ma, B. Qi, Y. Zhao, and H.-K. Lo, Practical Decoy State for Quantum Key Distribution, Phys. Rev. A 72, 012326 (2005)]

[K. Tamaki, M. Curty, and M. Lucamarini, Decoy-State Quantum Key Distribution with a Leaky Source, New J. Phys. 18, 065008 (2016)]

In [ ]:
def RdB_Decoy_err(dBloss,SigmaPhi,**var): 
  def GainDecoy_model(mu,pdc,eta): 
    # Ma et al: pdc for two detectors is around 2*pdc of single detector
    return 1- (1-pdc)*np.exp(-mu*eta) 

  def ErrorDecoy_model(mu,Q,pdc,eta,edet):
    # Ma et al: pdc for two detectors is around 2*pdc of single detector
    return (pdc/2 + (edet-pdc/2) * (1-np.exp(-mu*eta)))/Q 

  etad = var['DetectorEfficiency']*etadB(dBloss) # transmittance * efficiency of detection
  u = var['u']
  v = var['v']
  w = var['w']
  pdc = var['pdc']
  ephase = EphaseFromSigmaPhi(SigmaPhi)
  edet = var['edet']+ephase
  Qu = GainDecoy_model(u,pdc,etad)
  Qv = GainDecoy_model(v,pdc,etad)
  Qw = GainDecoy_model(w,pdc,etad)
  Eu = ErrorDecoy_model(u,Qu,pdc,etad,edet)
  Ev = ErrorDecoy_model(v,Qv,pdc,etad,edet)
  Ew = ErrorDecoy_model(w,Qw,pdc,etad,edet)
  
  expu = np.exp(u)
  expv = np.exp(v)
  expw = np.exp(w)
  
  Y0Lower = (v*Qw*expw-w*Qv*expv)/(v-w) # Lower bound for 0-photon yield
  Y1Lower = (u**2*(Qv*expv-Qw*expw)-(v**2-w**2)*(Qu*expu-Y0Lower))/(u*(u-v-w)*(v-w)) # Lower bound for 1-photon yield
  Qu1Lower = Y1Lower*u/expu
  
  e1Upper = (Ev*Qv*expv-Ew*Qw*expw)/((v-w)*Y1Lower) # Upper-bound for 1-photon errorate
  
  He1Upper = H2(e1Upper) # Binary Shannon entropy of 1photon error
  HEu = H2(Eu) # Binary Shannon entropy of total QBER
  
  return var['duty']*(Qu1Lower*(1-He1Upper)-Qu*var['fError']*HEu)

## Curty-Azuma-Lo (CAL) protocol

[M. Curty, K. Azuma, and H.-K. Lo, Simple Security Proof of Twin-Field Type Quantum Key Distribution Protocol, Npj Quantum Inf 5, 1 (2019)]

In [ ]:
def RdB_CAL_TF_QKD_err(dBloss,SigmaPhi,**var): 
  def Rlow(PZZ, f, eZ, eX):
    rr = 2*PZZ*(1-f*H2(eZ)-H2(min(0.5,eX)))
    return rr

  def pZZ(sqrtETA, alfa2, pdc, theta, phi):
    g = sqrtETA*alfa2
    omega = np.cos(theta)*np.cos(phi)
    pp = 1/2*(1-pdc)*(np.exp(-g*omega)+np.exp(g*omega))*np.exp(-g)-(1-pdc)**2*np.exp(-2*g)
    return pp

  def eZ(sqrtETA, alfa2, pdc, theta, phi):
    g = sqrtETA*alfa2
    omega = np.cos(theta)*np.cos(phi)
    ee = (np.exp(-g*omega)-(1-pdc)*np.exp(-g))/(np.exp(-g*omega)+np.exp(g*omega)-2*(1-pdc)*np.exp(-g))
    return min(1/2,ee)

  def summ(x, j, n_min, n_max):
    list = [x**(2*n+j)/math.sqrt(math.factorial(2*n+j)) for n in range(n_min,n_max)]
    s = sum(list)
    return s

  def Stot(x, j, n_min, n_max):
    sum1 = summ(x,j,n_min,n_max)
    Stott = np.exp(-x**2)*sum1**2
    return Stott

  def Deltaj(x, j, n_min, n_max, Xj):
    a = Stot(x, j, n_min, n_max)
    return a-Xj

  def C00(alfa2):
    temp = np.exp(-alfa2/2)
    return temp

  def C11(alfa2):
    temp = np.exp(-alfa2/2)*np.sqrt(alfa2)
    return temp

  def pXX(sqrtETA, pdc, qXX, nA, nB):
    temp = (1-pdc)*(pdc*(1-sqrtETA)**(nA+nB)+qXX)
    return temp

  def qXX11(sqrtETA, pdc, theta):
    temp01 = sqrtETA*(1-sqrtETA)/2
    temp10 = temp01
    temp11 = sqrtETA**2/4*np.cos(theta)**2
    temp = temp01+temp10+temp11
    return temp

  def qXX02(sqrtETA, pdc, theta): 
    temp01 = sqrtETA*(1-sqrtETA)
    temp11 = sqrtETA**2/4
    temp = temp01+temp11
    return temp

  def qXX22(sqrtETA, pdc, theta):
    temp01 = 2*sqrtETA*(1-sqrtETA)**3
    temp11 = (((sqrtETA**2)*(1-sqrtETA)**2)/4)*(2+4*(1+np.cos(theta)**2))
    temp12 = (sqrtETA**3*(1-sqrtETA)/8)*60
    temp22 = ((sqrtETA**4)/64)*384
    temp = temp01+temp11+temp12+temp22
    return temp

  def eX(sqrtETA, alfa2, pdc, theta, phi, nmin, nmax):
    qXX00 = 0
    temp0 = 1/pZZ(sqrtETA, alfa2, pdc, theta, phi)
    X0 = np.exp(-alfa2)*(1+np.sqrt(2)*alfa2+alfa2**2/2)
    X1 = np.exp(-alfa2)*(alfa2+2/np.sqrt(6)*alfa2**2)
    Delta0 = Deltaj(np.sqrt(alfa2), 0, nmin, nmax, X0)
    temp00 = C00(alfa2)**2*np.sqrt(pXX(sqrtETA, pdc, qXX00, 0, 0))+np.sqrt(2)*alfa2*np.sqrt(pXX(sqrtETA, pdc, qXX02(sqrtETA, pdc, theta), 0, 2))+(alfa2**2/2)*np.sqrt(pXX(sqrtETA, pdc, qXX22(sqrtETA, pdc, theta), 2, 2))+Delta0
    Delta1 = Deltaj(np.sqrt(alfa2), 1, nmin, nmax, X1)
    temp11 = C11(alfa2)**2*np.sqrt(pXX(sqrtETA, pdc, qXX11(sqrtETA, pdc, theta), 1, 1))+np.exp(-alfa2)*2/np.sqrt(6)*alfa2**2*1+Delta1
    temp = temp0*(temp00**2+temp11**2)
    return temp
  
  etaTF = var['DetectorEfficiency']*etadB(dBloss/2)
  eZZ = eZ(etaTF, var['alfa2'], var['pdc'], var['theta'], SigmaPhi)
  eXX = eX(etaTF, var['alfa2'], var['pdc'], var['theta'], SigmaPhi, var['n_min'], var['n_max'])
  pZZZ = pZZ(etaTF, var['alfa2'], var['pdc'], var['theta'], SigmaPhi)
  R = var["pZ"]**2*Rlow(pZZZ, var['fError'], eZZ, eXX)
  return R

## SNS with Active odd-parity pairing (AOPP)

[X.-B. Wang, Z.-W. Yu, and X.-L. Hu, Twin-Field Quantum Key Distribution with Large Misalignment Error, Phys. Rev. A 98, 062323 (2018)]

[Z.-W. Yu, X.-L. Hu, C. Jiang, H. Xu, and X.-B. Wang, Sending-or-Not-Sending Twin-Field Quantum Key Distribution in Practice, Sci Rep 9, 1 (2019)]

[M. Minder, M. Pittaluga, G. L. Roberts, M. Lucamarini, J. F. Dynes, Z. L. Yuan, and A. J. Shields, Experimental Quantum Key Distribution beyond the Repeaterless Secret Key Capacity, Nat. Photonics 13, 5 (2019)]

[H. Xu, Z.-W. Yu, C. Jiang, X.-L. Hu, and X.-B. Wang, Sending-or-Not-Sending Twin-Field Quantum Key Distribution: Breaking the Direct Transmission Key Rate, Phys. Rev. A 101, 042330 (2020)]

In [ ]:
def RdB_SNS_AOPP_TF_QKD_err(dBloss,SigmaPhi,**var): 
  def Gain_SNS_TFQKD_model(mu,pdc,etaTF):
    # from decoy states article by Ma et al: pdc for two detectors is around 2*pdc of single detector
    return 1- (1-pdc)**2*np.exp(-mu*etaTF) 

  def Error_SNS_TFQKD_model(mu,Q,pdc,etaTF,edet,ephase):
    etot = edet+ephase
    # from decoy states article by Ma et al: pdc for two detectors is around 2*pdc of single detector
    pdcma = pdc*2
    return (pdcma/2 + (etot-pdcma/2) * (1-np.exp(-mu*etaTF)))/Q 
  
  etaTF = var['DetectorEfficiency']*etadB(dBloss/2)
  eps = var['eps'] # Probability of one party sending versus not sending in Z window
  s = var['s'] # Intensity of sending signal from either A or B
  n = var['n'] # Intensity of not-sending signal
  
  # Intensity of decoy states from highest to lowest
  decoy2 = var['decoy2'] 
  decoy1 = var['decoy1'] 
  decoy0 = var['decoy0'] 
  
  pdc = var['pdc'] # probability of dark counts for a single detector, per pulse
  edet = var['edet'] # errorrate of detection if signal photons arrive
  ephase = EphaseFromSigmaPhi(SigmaPhi)
  
  ### Equations for decoy states
  Qdecoy2 = Gain_SNS_TFQKD_model(decoy2,pdc,etaTF)
  Qdecoy1 = Gain_SNS_TFQKD_model(decoy1,pdc,etaTF)
  Qdecoy0 = Gain_SNS_TFQKD_model(decoy0,pdc,etaTF)
  Edecoy1 = Error_SNS_TFQKD_model(decoy1,Qdecoy1,pdc,etaTF,edet,ephase)
  Edecoy0 = Error_SNS_TFQKD_model(decoy0,Qdecoy0,pdc,etaTF,edet,ephase)
  expdecoy2 = np.exp(decoy2)
  expdecoy1 = np.exp(decoy1)
  expdecoy0 = np.exp(decoy0)
  
  # Estimation of lower bound for 0-photon yield from Decoy states. This is valid also for Z windows
  Y0Lower = (decoy1*Qdecoy0*expdecoy0-decoy0*Qdecoy1*expdecoy1)/(decoy1-decoy0) # Lower bound for 0-photon yield
  Y1Lower = (decoy2**2*(Qdecoy1*expdecoy1-Qdecoy0*expdecoy0)-(decoy1**2-decoy0**2)*(Qdecoy2*expdecoy2-Y0Lower))/(decoy2*(decoy2-decoy1-decoy0)*(decoy1-decoy0))  # Lower bound for 1-photon yield
  # Estimation for upper bound of 1-photon phase-flip error. This is estimated with Decoy but applied to Z window 
  e1Upper = (Edecoy1*Qdecoy1*expdecoy1-Edecoy0*Qdecoy0*expdecoy0)/((decoy1-decoy0)*Y1Lower) # Upper-bound for 1-photon errorate
  
  # Ztilde window : send * notsend or notsend * send: possible candidate window to effectively transmit a signal,
  # provided a single click is detected
  pZtilde = eps*(1-eps) # A sends and B does not send
  psend0 = np.exp(-s)
  psend1 = s*np.exp(-s)
  pnotsend0 = np.exp(-n)
  pnotsend1 = n*np.exp(-n) 
  
  # 1-photon states are considered untagged (excess photons cannot be stolen without detection)
  Q1LowA = pZtilde*(psend1*pnotsend0+psend0*pnotsend1)*Y1Lower
  n11 = Q1LowA # single photon when A sends, B does not send, a single click is reported. To be estimated with decoy states
  n10 = n11 # single photon when B sends, A does not send, a single click is reported. To be estimated with decoy states

  # Gains: detected effective events given sent signals. They contain also multiphoton events
  # Both send and a click is detected
  Qu = Gain_SNS_TFQKD_model(s+s,pdc,etaTF) # Sum of both send intensities
  # A sends, B does not send
  QuA = Gain_SNS_TFQKD_model(s+n,pdc,etaTF)
  # B sends, A does not send and a click is detected
  QuB = QuA
  # Neither A nor B send but a click is detected
  Q0 = Gain_SNS_TFQKD_model(n+n,pdc,etaTF)
  Nc1 = pZtilde*QuA # A sends, B does not send, a single click is reported. Contains also multiphoton events. Estimated from a sample of discarded signals
  Nc0 = pZtilde*QuB # B sends, A does not send, a single click is reported. Contains also multiphoton events. Estimated from a sample of discarded signals
  Nd = eps**2*Qu # both A and B send and a single click is reported. Estimated from a sample of discarded signals
  Nv = (1-eps)**2*Q0 # neither A nor B send and a single click is reported. Estimated from a sample of discarded signals
  
  N0 = Nd+Nc0
  N1 = Nv+Nc1
  NA = min(N0,N1)
  Nvddv = (Nd/N0)*(Nv/N1)*NA
  Nc1c0 = (Nc0/N0)*(Nc1/N1)*NA
  
  Nttilde = Nc1c0+Nvddv
  Ezpp = Nvddv/Nttilde
  
  n1pp = (n10/N0)*(n11/N1)*NA
  e1Upperpp = 2*e1Upper*(1-e1Upper)
  
  overlap = var['pZ']**2 # both parties have to choose signal window (asymptotically pZ=1)
  
  R = overlap*( n1pp*(1-H2(e1Upperpp)) - var['fError']*Nttilde*H2(Ezpp) )
  return R

# Full setup and protocols' comparison

In [ ]:
# SOURCE and CHANNEL
parameters_source = {
 'clockrate' : 1.e9, # clock rate of source pulsed laser
 'stab_overhead' : 1000*1e-6 # 1ms realistic stabilization overhead
}
parameters_channels = {
 'alpha' : 0.2 # dB/km linear attenuation of standard optical fiber
}
parameters_decoy = {
 # Decoy-state TFQKD. u,v,w intensities of decoy states, as in Minder 2019
 'decoy_big' : 0.4,
 'decoy_medium' : 0.16,
 'decoy_mini' : 1e-5
}

# PROTOCOLS
parameters_protocols_common = {
 'fError' : 1.15 # Realistic error correction (in)efficiency as in Lucamarini 2018
}
parameters_protocols_SNS = {
 'pZ_SNS' : 1, # Probability of choosing the signal window is asymptotically 1
 'eps_SNS' : 0.04, # SNS probability of sending
 'eps_SNSAOPP' : 0.25
}
parameters_protocols_BB84 = {
 'duty_BB84' : 1 # BB84 with phase encoding. Asymptotically 1
}
parameters_protocols_CAL = {
 'pZ_CAL' : 1, # Asymptotically 1
 'nmin_CAL' : 0,
 'nmax_CAL' : 20,
 'u_CAL' : 0.018 # Optimal signal intensity in CAL (signal) in the range 0.015-0.04
}

parameters_protocols = {**parameters_protocols_common, **parameters_protocols_SNS, **parameters_protocols_BB84, **parameters_protocols_CAL}

# ALL COMMON PARAMETERS
parameters_common = {**parameters_source, **parameters_channels, **parameters_decoy, **parameters_protocols}

# DETECTORS
parameters_SPAD = {
'pDC' : 50/parameters_source['clockrate'], # pDC: detector Dark Counts
'etadet' : 0.25, #etadet detection efficiency
'errdet' : 0.02 # 2% polarization misalignment. Errorrate of detection if signal photons arrive
}
parameters_SNSPD = {
'pDC' : 10/parameters_source['clockrate'], 
'etadet' : 0.90, 
'errdet' : 0.02 
}

def plot_panel_scenarios(comm, cavity, stab, deltaL, dBloss, sigma_lim, fig, ax,panellabel, **var):
  
  theta_misalignment = 2*np.arcsin(np.sqrt(var['errdet'])) # convert from errdet to polarization misalignment

  cmap = mpl.colormaps["Set1"]
  colors = cmap.colors 
  ax.set_prop_cycle(color = colors)
  
  allconfig  = [calc_sigma_tau_loss(comm, cavity, stab, deltaL, dBlossi, var['alpha'], sigma_lim) for dBlossi in dBloss]
  
  la = "Realistic PLOB bound"
  rates = [var['clockrate']*RdB_realistic_secret_key_capacity(dBlossi,var['etadet']) for (tauQ, deltaL, sigma_phi, dBlossi) in allconfig]
  ax.plot(dBloss,rates,label = la,linestyle = "-",linewidth = 1.5)

  la = "Decoy states BB84"
  varDecoy = {
    'u' : var['decoy_big'],
    'v' : var['decoy_medium'],
    'w' : var['decoy_mini'],
    'pdc' : var['pDC'],
    'DetectorEfficiency' : var['etadet'],
    'edet' : var['errdet'],
    'fError' : var['fError'],
    'duty' : var['duty_BB84']
  }
  # We consider phase noise to be irrelevant in BB84
  rates = [var['clockrate']*RdB_Decoy_err(dBlossi,SigmaPhi=0,**varDecoy) for (tauQ, deltaL, sigma_phi, dBlossi) in allconfig]
  ax.plot(dBloss,rates,label = la,linestyle = (0,(1,1)),linewidth = 2.5)
  
  la = "SNS-AOPP"
  varSNS = {
    'eps' : var['eps_SNSAOPP'],
    's' : var['decoy_big']/2,
    'n' : var['decoy_mini']/2,
    'pZ' : var['pZ_SNS'],
    'decoy2' : var['decoy_big'], # Notice: sum of intensities from A and B (s)
    'decoy1' : var['decoy_medium'],
    'decoy0' : var['decoy_mini'],
    'pdc' : var['pDC'], 
    'DetectorEfficiency': var['etadet'],
    'edet' : var['errdet'],
    'fError' : var['fError']
  }
  rates = [var['clockrate']*duty_stabilization(tauQ,var['stab_overhead'])*RdB_SNS_AOPP_TF_QKD_err(dBlossi,sigma_phi,**varSNS) for (tauQ, deltaL, sigma_phi, dBlossi) in allconfig]
  ax.plot(dBloss,rates,label = la,linestyle = (0,(4,1)),linewidth = 2.5)
  
  la = "CAL"
  varCAL = {
    'n_min' : var['nmin_CAL'],
    'n_max' : var['nmax_CAL'],
    'fError' : var['fError'],
    'pZ' : var['pZ_CAL'],
    'pdc' : var['pDC'],
    'DetectorEfficiency': var['etadet'],
    'theta' : theta_misalignment, 
    'alfa2' : var['u_CAL']
    }
  rates = [var['clockrate']*duty_stabilization(tauQ,var['stab_overhead'])*RdB_CAL_TF_QKD_err(dBlossi,sigma_phi,**varCAL) for (tauQ, deltaL, sigma_phi, dBlossi) in allconfig]
  ax.plot(dBloss,rates,label = la,linestyle = (0,(1,2,4,2)),linewidth = 2.5) 

  ax.annotate(panellabel,xy = (18,50),fontsize = fsize,backgroundcolor = "w")


def plot_4panels_graph_db(dBmin,dBmax,minrate,maxrate,**var):
  rows = 2
  cols = 2
  fig, axs = plt.subplots(rows,cols, figsize = (10.5, 5.2))
  
  def loss2L(loss):
    return loss/var['alpha']
  def L2loss(L):
    return var['alpha']*L
  
  for row in range(rows):
    for col in range(cols):
      axs[row,col].set_xlim(dBmin,dBmax)
      axs[row,col].set_ylim(minrate,maxrate)
      axs[row,col].set_yscale('log')
      axs[row,col].yaxis.set_major_locator(mticker.LogLocator(numticks = 999))
      axs[row,col].yaxis.set_minor_locator(mticker.LogLocator(numticks = 999, subs = "auto"))
      
      axs[row,col].grid(color = (0.9, 0.9, 0.9))
      axs[row,col].tick_params(direction="in", which='both')

  axs[0,0].set_ylabel(r"Key rate [bit s$^{-1}$]")
  axs[0,0].yaxis.set_label_coords(-0.12, -.08)
  secax = axs[0,0].secondary_xaxis('top', functions = (loss2L,L2loss), zorder=2)
  secax.tick_params(axis="x",direction="in", which='both')
  
  axs[0,0].xaxis.set_ticklabels([]) 

  secax1 = axs[0,1].secondary_xaxis('top', functions = (loss2L,L2loss), zorder=2)
  secax1.tick_params(axis="x",direction="in", which='both')
  axs[0,1].xaxis.set_ticklabels([])
  axs[0,1].yaxis.set_ticklabels([])
  
  axs[1,0].set_xlabel("Alice-Bob channel loss [dB]")
  axs[1,0].xaxis.set_label_coords(1.05, -.15)
  
  axs[1,1].yaxis.set_ticklabels([])
   
  dBloss = np.linspace(dBmin,dBmax,200)
  
  sigma_lim=max_sigma_phi
  ScenPanA=Scenario4
  plot_panel_scenarios(ScenPanA["comm"], ScenPanA["cavity"], ScenPanA["stab"], ScenPanA["deltaL"], dBloss, sigma_lim, fig,axs[0,0],panellabel = "a) Scenarios 1, 4",**var)
  ScenPanB=Scenario5
  plot_panel_scenarios(ScenPanB["comm"], ScenPanB["cavity"], ScenPanB["stab"], ScenPanB["deltaL"], dBloss, sigma_lim, fig,axs[0,1],panellabel = "b) Scenarios 2, 5, 7",**var)
  ScenPanC=Scenario3
  plot_panel_scenarios(ScenPanC["comm"], ScenPanC["cavity"], ScenPanC["stab"], ScenPanC["deltaL"], dBloss, sigma_lim, fig,axs[1,0],panellabel = "c) Scenario 3",**var)
  ScenPanD=Scenario6
  plot_panel_scenarios(ScenPanD["comm"], ScenPanD["cavity"], ScenPanD["stab"], ScenPanD["deltaL"], dBloss, sigma_lim, fig,axs[1,1],panellabel = "d) Scenario 6",**var)
  
  axs[0,0].legend(fontsize = legfontsize, loc = (0.5,0.5), frameon = "true") 
  fig.suptitle('Equivalent fiber length [km]',fontsize = fsize)

  fig.tight_layout()
  plt.subplots_adjust(left = 0.1, bottom = 0.1, right = 0.9, top = 0.9, wspace = 0.07, hspace = 0.1)

  return fig

## Key rates with SPAD FIGURE 3

In [ ]:
parameters = { **parameters_common, **parameters_SPAD}

fig = plot_4panels_graph_db(dBmin = 15,dBmax = 110,minrate = 1e1,maxrate = 1e7,**parameters)

plt.savefig(f"tfcomparison_4panels_SPAD.pdf", bbox_inches = 'tight')

## Key rates with SNSPD FIGURE 4

In [ ]:
parameters = { **parameters_common, **parameters_SNSPD}

fig = plot_4panels_graph_db(dBmin = 15,dBmax = 110,minrate = 1e1,maxrate = 1e7,**parameters)

plt.savefig(f"tfcomparison_4panels_SNSPD.pdf", bbox_inches = 'tight')